In [2]:
from copy import deepcopy
from collections import defaultdict
import random

## Reading and initializing functions

In [3]:
def get_states(filename, sudokusize=9):
    '''
    get_states is to read multiple sudokus in the format:
    ..8..4..5...64..5 etc.
    '''
    sudokus = []
    with open(filename) as sudoku_states:
        for state in sudoku_states:
            sudoku = []
            row = 1
            for i, content in enumerate(state):
                if i%sudokusize == 0 and i > 0:
                    row+=1
                try:
                    int(content)
                    clause = int(str(row) + str(i%sudokusize+1) + content)
                    sudoku.append(clause)
                except:
                    # is not convertible to int
                    continue
            sudokus.append(sudoku)
    return sudokus

def get_state_from_dimacs(filename, sudokusize=9):
    '''
    This function reads a sudoku state in dimacs format
    '''
    state = []
    with open(filename) as f:
        for clause in f:
            for literal in clause.split():
                if literal!= '0':  
                    state.append(int(literal))
    return state

def get_rules(filename):
    constraints = {} # dictionary with constraints as: clausenumber->[literals]
    pointers = {} # dictionary with pointers to clause numbers for literals as: literals->[clausenumbers]
    with open(filename) as sudoku_rules:
        for index, clause in enumerate(sudoku_rules):
            if index == 0:
                continue # skip first line
            constraints[index]=[]
            for literal in clause.split():
                lit = int(literal)
                if lit!=0:
                    constraints[index].append(lit)
                    if lit not in pointers.keys():
                        pointers[lit]=[index]
                    else:
                        pointers[lit].append(index)
                    
    return constraints, pointers

## DP helper functions for constraints updates

In [182]:
def assign_literal(constraints, pointers, literal, assignments):
    '''
    assign the given literal to be True.
    assignLiteral is aimed to be one recursion stack, so deepcopies are made
    in order to properly backtrack
    '''
#     print(literal)
    constraintsCopied = deepcopy(constraints)
    pointersCopied = deepcopy(pointers)
    assignmentsCopied = deepcopy(assignments)
    assignmentsUpdated = update_assigments(assignmentsCopied, literal)
    constraintsUpdated, pointersUpdated = update_constraints(constraintsCopied, pointersCopied, literal)
    return constraintsUpdated, pointersUpdated, assignmentsUpdated
     
def update_constraints(constraints, pointers, literal):
    
    ## Find clauses with literal and remove them
    try:
        clauses = list(pointers[literal])
        for clause in clauses:
            for lit in constraints[clause]:
                pointers[lit].remove(clause)
            del constraints[clause]
        del pointers[literal]
    except:
        print("nonoo")
    
    ## Find clauses with counter-literal and remove its counter-literal
    try:
        counterLiteral = -literal
        clauses = list(pointers[counterLiteral])
        del pointers[counterLiteral]
        for clause in clauses:
            constraints[clause].remove(counterLiteral)
    except:
        return constraints, pointers

    return constraints, pointers

def update_assigments(assignments, literal):
    if literal in assignments:
        print("already assigned", literal, "(in this stack), returning...")
        return assignments
    else:
        assignments.append(literal)
        return assignments
    
def check_tautologies(constraints, pointers):
    foundOne = False
    for clause in constraints.keys():
        literals = constraints[clause]
        counterLiterals = [-x for x in literals]
        for i in literals:
            for j in counterLiterals:
                if i == j:
                    del constraints[clause]
                    pointers[i].remove(clause)
                    foundOne = True
                    break
    if foundOne:
        print("Found tautologies and removed corresponding clauses")
    else:
        print("No tautologies found")
                  
    return constraints, pointers  

## DP cases

In [163]:
def empty_clause(constraints):
    for clause in constraints.keys():
        if not constraints[clause]:
            print(clause, constraints[clause])
            return True
        
    return False

def unit_clause(constraints): 
    for clause in constraints.keys():
        if len(constraints[clause])==1:
            literal = constraints[clause][0]
#             print("found unit clause with literal", literal)
            return literal

    return False

def pure_literal(literals):
    for literal in literals:
        if -literal not in literals:
            print("found pure literal", literal)
            return literal
        
    return False

def random_literal(literals): 
    literal = random.choice(literals)
    print("assigning random literal", literal)  
    return literal

## DP main function

In [176]:
def DP(constraints, pointers, assignments):
    
    if len(constraints)==0:
        return True
   
    if empty_clause(constraints):
        print("found empty clause")
        return False
    
    all_literals = list(pointers.keys())
    print(len(all_literals))
    
    literal = unit_clause(constraints)
    if literal:
        constraints, pointers, assignments = assign_literal(constraints, pointers, literal, assignments)
#         print("updated pointers to", literal, pointers[literal])
        DP(constraints, pointers, assignments)
        
    literal = pure_literal(all_literals)
    if literal:
        constraints, pointers, assignments = assign_literal(constraints, pointers, literal, assignments)
        DP(constraints, pointers, assignments)
                
    literal = random_literal(all_literals)
    constraints, pointers, assignments = assign_literal(constraints, pointers, literal, assignments)
    if DP(constraints, pointers, assignments):
        return True
    else:
        constraints, pointers, assignments = assign_literal(constraints, pointers, -literal, assignments)
        DP(constraints, pointers, assignments)

In [ ]:
def set_up():
    
    ## Get board and rules
    state = get_state_from_dimacs('sudoku-example.txt')
#     state = get_states('1000 sudokus.txt')[2]
    print("Sudoku initial board state", state)
    constraints, pointers = get_rules('sudoku-rules.txt')
    print("326", constraints[326])
    print("Length of clauses:", len(constraints))
    
    ## Update constraints according to initial board state
    initial_assignments = []
    for literal in state:
        constraints, pointers, initial_assignments = assign_literal(constraints, pointers, literal, initial_assignments)
    print("clauses after board state:", len(constraints.keys()))
    
    ## Check tautologies
    constraints, pointers = check_tautologies(constraints, pointers)
    
    ## Run DP
    print("Starting DP algorithm...")
    
    succes = DP(constraints, pointers, initial_assignments)
    if succes:
        print("Solution found")
    else:
        print("No solution found")
        
set_up()
    

Sudoku initial board state [168, 175, 225, 231, 318, 419, 444, 465, 493, 689, 692, 727, 732, 828, 886, 956, 961, 973]
326 [-195, -198]
Length of clauses: 11988
clauses after board state: 11916
No tautologies found
Starting DP algorithm...
1422
1420
1418
1416
1414
1412
1410
1408
1406
1404
1402
1400
1398
1396
1394
1392
1390
1388
1386
1384
1382
1380
1378
1376
1374
1372
1370
1368
1366
1364
1362
1360
1358
1356
1354
1352
1350
1348
1346
1344
1342
1340
1338
1336
1334
1332
1330
1328
1326
1324
1322
1320
1318
1316
1314
1312
1310
1308
1306
1304
1302
1300
1298
1296
1294
1292
1290
1288
1286
1284
1282
1280
1278
1276
1274
1272
1270
1268
1266
1264
1262
1260
1258
1256
1254
1252
1250
1248
1246
1244
1242
1240
1238
1236
1234
1232
1230
1228
1226
1224
1222
1220
1218
1216
1214
1212
1210
1208
1206
1204
1202
1200
1198
1196
1194
1192
1190
1188
1186
1184
1182
1180
1178
1176
1174
1172
1170
1168
1166
1164
1162
1160
1158
1156
1154
1152
1150
1148
1146
1144
1142
1140
1138
1136
1134
1132
1130
1128
1126
1124
1122
1120
1

already assigned 897 (in this stack), returning...
nonoo
assigning random literal 895
nonoo
2
assigning random literal 897
already assigned 897 (in this stack), returning...
nonoo
assigning random literal 895
5822 []
found empty clause
nonoo
5822 []
found empty clause
assigning random literal -895
4
2
assigning random literal -948
already assigned -948 (in this stack), returning...
nonoo
assigning random literal -948
assigning random literal 895
5822 []
found empty clause
nonoo
5822 []
found empty clause
assigning random literal -947
8881 []
found empty clause
nonoo
8881 []
found empty clause
assigning random literal -947
8881 []
found empty clause
nonoo
8881 []
found empty clause
assigning random literal 847
12
5477 []
found empty clause
assigning random literal 845
nonoo
5477 []
found empty clause
already assigned -845 (in this stack), returning...
nonoo
5477 []
found empty clause
nonoo
12
5477 []
found empty clause
assigning random literal -948
5477 []
found empty clause
nonoo
5477 

nonoo
assigning random literal 845
already assigned 845 (in this stack), returning...
nonoo
8
6
4
2
assigning random literal 948
nonoo
assigning random literal 948
2810 []
found empty clause
nonoo
2810 []
found empty clause
assigning random literal -748
nonoo
4
2
assigning random literal -948
already assigned -948 (in this stack), returning...
nonoo
assigning random literal 948
2810 []
found empty clause
nonoo
2810 []
found empty clause
already assigned 748 (in this stack), returning...
nonoo
4
2
assigning random literal 948
nonoo
assigning random literal 948
2810 []
found empty clause
nonoo
2810 []
found empty clause
assigning random literal 748
4
2
assigning random literal -948
already assigned -948 (in this stack), returning...
nonoo
assigning random literal -948
assigning random literal -897
2628 []
found empty clause
nonoo
2628 []
found empty clause
assigning random literal -847
14
12
10
8
6
4
2
assigning random literal 897
already assigned 897 (in this stack), returning...
nonoo


found empty clause
assigning random literal -788
8252 []
found empty clause
nonoo
8252 []
found empty clause
already assigned -947 (in this stack), returning...
nonoo
14
12
11471 []
found empty clause
assigning random literal -897
11471 []
found empty clause
nonoo
11471 []
found empty clause
assigning random literal -998
11915 []
found empty clause
nonoo
11915 []
found empty clause
assigning random literal 997
14
11915 []
found empty clause
assigning random literal -785
11471 []
found empty clause
nonoo
11471 []
found empty clause
nonoo
14
11915 []
found empty clause
assigning random literal 947
5575 []
found empty clause
nonoo
5575 []
found empty clause
assigning random literal -948
5588 []
found empty clause
nonoo
5588 []
found empty clause
assigning random literal 788
11595 []
found empty clause
nonoo
11595 []
found empty clause
assigning random literal 897
24
22
20
18
16
14
12
10
8
6
4
2
assigning random literal 948
nonoo
assigning random literal 948
2810 []
found empty clause
nono

already assigned -788 (in this stack), returning...
nonoo
4
2
assigning random literal 998
already assigned 998 (in this stack), returning...
nonoo
assigning random literal -998
2961 []
found empty clause
nonoo
2961 []
found empty clause
nonoo
4
2
assigning random literal -998
nonoo
assigning random literal -998
2961 []
found empty clause
nonoo
2961 []
found empty clause
assigning random literal -997
4
2
assigning random literal -998
nonoo
assigning random literal 998
assigning random literal -785
5810 []
found empty clause
nonoo
5810 []
found empty clause
nonoo
12
10
8
6
4
2
assigning random literal 998
already assigned 998 (in this stack), returning...
nonoo
assigning random literal -997
already assigned -997 (in this stack), returning...
nonoo
2
assigning random literal 998
already assigned 998 (in this stack), returning...
nonoo
assigning random literal 998
2
assigning random literal 997
nonoo
assigning random literal 788
2287 []
found empty clause
nonoo
2287 []
found empty clause


...

11555 []
found empty clause
assigning random literal -895
8474 []
found empty clause
nonoo
8474 []
found empty clause
assigning random literal -785
11471 []
found empty clause
nonoo
11471 []
found empty clause
nonoo
30
28
26
24
22
11833 []
found empty clause
assigning random literal -288
11833 []
found empty clause
nonoo
11833 []
found empty clause
assigning random literal -798
11915 []
found empty clause
nonoo
11915 []
found empty clause
assigning random literal 798
22
11656 []
found empty clause
assigning random literal -895
8474 []
found empty clause
nonoo
8474 []
found empty clause
nonoo
22
11656 []
found empty clause
assigning random literal -781
5662 []
found empty clause
nonoo
5662 []
found empty clause
assigning random literal -387
24
22
11833 []
found empty clause
assigning random literal 791
11833 []
found empty clause
nonoo
11833 []
found empty clause
assigning random literal 788
20
18
11471 []
found empty clause
assigning random literal 288
11471 []
found empty clause
nonoo

14
12
11471 []
found empty clause
assigning random literal 788
11471 []
found empty clause
nonoo
11471 []
found empty clause
assigning random literal -997
8881 []
found empty clause
nonoo
8881 []
found empty clause
assigning random literal -791
nonoo
14
12
11471 []
found empty clause
assigning random literal 998
8944 []
found empty clause
nonoo
8944 []
found empty clause
assigning random literal -895
8474 []
found empty clause
nonoo
8474 []
found empty clause
already assigned 791 (in this stack), returning...
nonoo
14
12
11471 []
found empty clause
assigning random literal -788
2258 []
found empty clause
nonoo
2258 []
found empty clause
assigning random literal -788
8252 []
found empty clause
nonoo
8252 []
found empty clause
assigning random literal 785
8166 []
found empty clause
nonoo
8166 []
found empty clause
nonoo
18
16
14
12
11471 []
found empty clause
assigning random literal 785
nonoo
11471 []
found empty clause
already assigned -785 (in this stack), returning...
nonoo
11471 []


found empty clause
assigning random literal -785
11471 []
found empty clause
nonoo
11471 []
found empty clause
nonoo
10
11915 []
found empty clause
assigning random literal -788
5921 []
found empty clause
nonoo
5921 []
found empty clause
nonoo
14
12
11471 []
found empty clause
assigning random literal -997
8881 []
found empty clause
nonoo
8881 []
found empty clause
assigning random literal 998
8944 []
found empty clause
nonoo
8944 []
found empty clause
assigning random literal 795
8167 []
found empty clause
nonoo
8167 []
found empty clause
assigning random literal -948
2776 []
found empty clause
nonoo
2776 []
found empty clause
assigning random literal -788
8252 []
found empty clause
nonoo
8252 []
found empty clause
nonoo
22
20
18
16
14
12
11471 []
found empty clause
assigning random literal -788
2258 []
found empty clause
nonoo
2258 []
found empty clause
assigning random literal 897
8574 []
found empty clause
nonoo
8574 []
found empty clause
assigning random literal -998
11915 []
foun

11915 []
found empty clause
assigning random literal 895
11833 []
found empty clause
nonoo
11833 []
found empty clause
assigning random literal 997
22
20
11915 []
found empty clause
assigning random literal -947
11915 []
found empty clause
nonoo
11915 []
found empty clause
assigning random literal 895
11833 []
found empty clause
nonoo
11833 []
found empty clause
nonoo
22
20
11915 []
found empty clause
assigning random literal -788
5921 []
found empty clause
nonoo
5921 []
found empty clause
assigning random literal -897
18
11833 []
found empty clause
assigning random literal -791
11656 []
found empty clause
nonoo
11656 []
found empty clause
nonoo
18
11833 []
found empty clause
assigning random literal 781
11329 []
found empty clause
nonoo
11329 []
found empty clause
assigning random literal -781
24
22
20
18
16
14
12
11471 []
found empty clause
assigning random literal 997
11471 []
found empty clause
nonoo
11471 []
found empty clause
assigning random literal 998
8944 []
found empty claus

2258 []
found empty clause
assigning random literal -895
8474 []
found empty clause
nonoo
8474 []
found empty clause
assigning random literal -895
8474 []
found empty clause
nonoo
8474 []
found empty clause
nonoo
16
14
12
11471 []
found empty clause
assigning random literal 897
8574 []
found empty clause
nonoo
8574 []
found empty clause
assigning random literal -795
already assigned -795 (in this stack), returning...
nonoo
12
11471 []
found empty clause
assigning random literal -897
11471 []
found empty clause
nonoo
11471 []
found empty clause
nonoo
12
11471 []
found empty clause
assigning random literal 785
nonoo
11471 []
found empty clause
already assigned -785 (in this stack), returning...
nonoo
11471 []
found empty clause
assigning random literal 788
11595 []
found empty clause
nonoo
11595 []
found empty clause
assigning random literal -795
18
16
14
12
11471 []
found empty clause
assigning random literal 897
8574 []
found empty clause
nonoo
8574 []
found empty clause
assigning rand